# 1_Markdown 

環境設置，default位置查詢，SparkContext object建立



In [1]:
#Build object pyspark context as the extrance to launch main
import findspark
findspark.init

!pip install pyspark
from pyspark.context import SparkContext,SparkConf
import os
import sys
from pyspark.rdd import RDD

#若沒有下面這段
#會有Exception: Java gateway process exited before sending its port number
#Config
os.environ['JAVA_HOME'] = 'C:\Program Files\Java\jre1.8.0_301'
os.environ['PYSPARK_PYTHON'] = sys.executable
os.environ['PYSPARK_DRIVER_PYTHON'] = sys.executable


You should consider upgrading via the 'c:\users\leoshr\appdata\local\programs\python\python39\python.exe -m pip install --upgrade pip' command.


In [2]:
sc = SparkContext(conf=SparkConf().setAppName("matrix_machine").setMaster("local"))
sc

<SparkContext master=local appName=matrix_machine>

In [3]:
os.getcwd()

'C:\\Users\\LeoShr\\MDA\\Hw1'

# 2_Markdown

1. 將檔案input.txt 讀入，切成分別為M開頭的matrix_one  的list 與N開頭的 matrix_two list

2. 依照element後切分成兩份txt檔案再存到本機端，再當作兩個matrix RDD檔案匯入(因為不知道RDD怎麼切)。

3. 分別存檔成m1.txt, m2.txt
4. 將已經拆分的兩份txt matrix檔案以RDD形式讀入



In [4]:
#讀入有 '\n' 並依照M, N拆成兩筆list

with open('C:///Users/LeoShr/MDA/Hw1///input.txt','r') as f:
    contents = [x for x in f.readlines()]    
    
#切割text file，分別為M開頭的matrix_one  的list 與N開頭的 matrix_two list
matrix_one =[]
matrix_two = []
for ele in contents:
    if ele[0] == 'M':
        matrix_one.append(ele)
    elif(ele[0] == 'N'):
        matrix_two.append(ele)



#讀入沒有 '\n' #依照M, N拆成兩筆text file

# with open('C:///Users/LeoShr/MDA///matrix_com.txt','r') as f:
#     contents = [x.rstrip("\n") for x in f.readlines()]       
# contents

In [5]:
#default matrix_one, matrix_two會丟到C:\Users\LeoShr\MDA\，並分別命名為m1.txt,m2.txt 

#分別存檔成m1.txt, m2.txt
def save_the_txt_file(lines):
    path_1 = 'C:///Users/LeoShr/MDA///m1.txt'
    path_2 = 'C:///Users/LeoShr/MDA///m2.txt'
    assert (lines == matrix_one)| (lines == matrix_two),'InputError:only matrix_one/matrix_two are acceptable'
    if lines == matrix_one:
        f = open(path_1, 'w')
        f.writelines(lines)
        f.close()
    elif(lines == matrix_two):
        f = open(path_2, 'w')
        f.writelines(lines)
        f.close()       
        

save_the_txt_file(matrix_one)
save_the_txt_file(matrix_two)

In [6]:
#將已經拆分的兩份txt matrix檔案以RDD讀入
path_1 = 'file:///C:/Users/LeoShr/MDA///m1.txt'
matrix_1  =sc.textFile(path_1)

path_2 = 'file:///C:/Users/LeoShr/MDA///m2.txt'
matrix_2 = sc.textFile(path_2)

#words =sc.textFile(name = 'file://' + path)
print(f'matrix_1:\n{matrix_1}\nmatrix_2:\n{matrix_2}')

matrix_1:
file:///C:/Users/LeoShr/MDA///m1.txt MapPartitionsRDD[1] at textFile at <unknown>:0
matrix_2:
file:///C:/Users/LeoShr/MDA///m2.txt MapPartitionsRDD[3] at textFile at <unknown>:0


# 3_Markdown

1. 看看兩個切好的RDD檔，前20個檔案看看

In [7]:
n = 20
print(f'matrix_1前{n}個:\n{matrix_1.take(n)}')
print(f'matrix_2前{n}個:\n{matrix_2.take(n)}')


matrix_1前20個:
['M,0,0,177', 'M,0,1,470', 'M,0,2,388', 'M,0,3,241', 'M,0,4,141', 'M,0,5,47', 'M,0,6,24', 'M,0,7,14', 'M,0,8,472', 'M,0,9,425', 'M,0,10,104', 'M,0,11,317', 'M,0,12,261', 'M,0,13,243', 'M,0,14,146', 'M,0,15,242', 'M,0,16,448', 'M,0,17,131', 'M,0,18,220', 'M,0,19,194']
matrix_2前20個:
['N,0,0,117', 'N,0,1,376', 'N,0,2,421', 'N,0,3,241', 'N,0,4,342', 'N,0,5,451', 'N,0,6,450', 'N,0,7,97', 'N,0,8,364', 'N,0,9,37', 'N,0,10,329', 'N,0,11,128', 'N,0,12,129', 'N,0,13,253', 'N,0,14,328', 'N,0,15,148', 'N,0,16,318', 'N,0,17,362', 'N,0,18,477', 'N,0,19,180']


# 4_Markdown

1.  建立to_matrix_a(x)，分別將matrix a 依照','分割成'matrix 字母','row','col','value'，並回傳['col',('row','val')], 以col 為key
2. 建立to_matrix_b(x)，分別將matrix b 依照','分割成'matrix 字母','row','col','value'，並回傳['row',('col','val')], 以row 為key

矩陣相乘時，matrix_a.col == matrix_b.row; matrix_a.row = matrix_b.col

In [8]:
#split string to (column, (row, value))
def to_matrix_a(x):
    m,i, j, v = x.split(',')
    return (j, (i, v))
#split string to (row, (column, value))
def to_matrix_b(x):
    m,j, k, v = x.split(',')
    return (j, (k, v))

# 5_Markdown

1. 實際執行map，將matrix_1 rdd依照 to_matrix_a 的function 做map，並assigned as entrance_a
2. 實際執行map，matrix_2 rdd依照 to_matrix_b 的function 做map，並assigned as entrance_b

3. 觀察一下 entrance_a.collect()  <- 形式(column, (row, value))
4.  觀察一下 entrance_b.collect() <- 形式(row, (column, value))


5. multiply_mat是最後用來map的function，用途在於使用join好的RDD依照function進行取值，回傳((row,col),(value))的format  

In [9]:
# entrance_a = matrix_1.flatMap(to_matrix_a)
# entrance_b = matrix_2.flatMap(to_matrix_b)
entrance_a = matrix_1.map(to_matrix_a)

entrance_b = matrix_2.map(to_matrix_b)


In [10]:
# entrance_a.collect()
# #(column, (row, value))
# entrance_b.collect()
# #(row, (column, value))

In [11]:
#邏輯 a.col == b.row; a.row == b.col

def multiply_mat(x):
    i, v = x[1][0]
    #print(f'x[1][0]::x:{x}\ni:{i},v:{v}\n\n')
    k, w = x[1][1]
    #print(f'x[1][1]::x:{x}\nk:{k},w:{w}\n\n')

    return ((i, k), (int(v) * int(w)))

# Final_Markdown

1. 將rdd entrance_a 與 entrance_b 以a之key join成同一張RDD後，拿該RDD丟到function- multiply_mat中，取得((i, k), 相乘的值)
2. operator.add 會輸入x, y, return (x+y), 該x與y 來自.map(multiply_mat)之後的結果 
3. reduceByKey(operator.add)  則在將RDD依照key相加(operator.add)(Basically, we've acheve the goal here already)
4. 最後依據function format 回傳 (r,c,v) 避免輸出的位置亂跳
5. 使用collect得到rdd

In [12]:
#依照 sql join 設計的
import operator
from pyspark.mllib.linalg.distributed import CoordinateMatrix, MatrixEntry
from pyspark.sql import SparkSession


#將rdd entrance_a 與 entrance_b 以a之key join成同一張RDD後，拿該RDD丟到function- multiply_mat中，取得((i, k), 相乘的值)
#operator.add 會輸入x, y, return (x+y), 該x與y 來自.map(multiply_mat)之後的結果 
#reduceByKey(operator.add)  則在將RDD依照key相加(operator.add)(Basically, we've acheve the goal here already)
#最後依據function format 回傳 (r,c,v) 避免輸出的位置亂跳

product_entries = entrance_a \
    .join(entrance_b) \
    .map(multiply_mat) \
    .reduceByKey(operator.add) \
    .map(lambda x:  (x[0][0], x[0][1], x[1]))

In [13]:
output = product_entries.collect()
output

[('0', '0', 28322872),
 ('0', '1', 31821693),
 ('0', '4', 30590919),
 ('0', '8', 30701980),
 ('0', '9', 29697452),
 ('0', '10', 30308892),
 ('0', '12', 28157956),
 ('0', '14', 30701599),
 ('0', '16', 30506907),
 ('0', '17', 29579830),
 ('0', '19', 27473242),
 ('0', '20', 29788171),
 ('0', '21', 31146433),
 ('0', '22', 29338649),
 ('0', '24', 29671360),
 ('0', '26', 30490404),
 ('0', '29', 29944454),
 ('0', '33', 29597770),
 ('0', '34', 29209535),
 ('0', '40', 27780584),
 ('0', '44', 29650899),
 ('0', '45', 30748820),
 ('0', '48', 31271224),
 ('0', '50', 31845761),
 ('0', '53', 32047881),
 ('0', '54', 28720338),
 ('0', '56', 31047550),
 ('0', '57', 30660508),
 ('0', '60', 28724555),
 ('0', '63', 30431962),
 ('0', '64', 29132897),
 ('0', '66', 30246403),
 ('0', '68', 29749932),
 ('0', '69', 29755167),
 ('0', '70', 28808281),
 ('0', '73', 30517039),
 ('0', '74', 29295927),
 ('0', '77', 29673026),
 ('0', '82', 28852424),
 ('0', '83', 28907238),
 ('0', '84', 28989478),
 ('0', '86', 29780669

In [14]:
len(product_entries.collect()) #250000

250000

# Save the output as a text file
- 用with遇到城市會自動close問題   solution: 換行手動寫入txt檔
- 遇到turple 內int無法iterate問題，因此採用concate(+) solution: 連接轉成str的值，

In [15]:
fp = open('output.txt', 'w')
for element in output:
    jj = element[0]+','+element[1]+','+str(element[2])
    #print(jj)
    fp.write(jj+'\n')
        
fp.close()              

0,0,28322872
0,1,31821693
0,4,30590919
0,8,30701980
0,9,29697452
0,10,30308892
0,12,28157956
0,14,30701599
0,16,30506907
0,17,29579830
0,19,27473242
0,20,29788171
0,21,31146433
0,22,29338649
0,24,29671360
0,26,30490404
0,29,29944454
0,33,29597770
0,34,29209535
0,40,27780584
0,44,29650899
0,45,30748820
0,48,31271224
0,50,31845761
0,53,32047881
0,54,28720338
0,56,31047550
0,57,30660508
0,60,28724555
0,63,30431962
0,64,29132897
0,66,30246403
0,68,29749932
0,69,29755167
0,70,28808281
0,73,30517039
0,74,29295927
0,77,29673026
0,82,28852424
0,83,28907238
0,84,28989478
0,86,29780669
0,88,30259520
0,91,30599032
0,93,30407913
0,96,30442243
0,98,29708082
0,100,29516761
0,102,29611712
0,106,29176408
0,107,30574222
0,108,30308635
0,110,29926048
0,111,29404826
0,112,30847114
0,113,28542466
0,115,30258467
0,116,29876477
0,119,28657721
0,121,30314547
0,122,30351985
0,128,29399562
0,130,29170094
0,132,29350965
0,134,30435182
0,138,29435312
0,139,28851070
0,140,29676070
0,141,28076338
0,143,29761000
0,

19,162,32943195
19,163,31803992
19,164,31391260
19,167,30987099
19,173,32835694
19,174,30923375
19,175,30620403
19,179,32634047
19,180,29836966
19,184,32046394
19,185,33232880
19,188,32661777
19,189,30119218
19,190,31934498
19,192,30663577
19,198,32844871
19,202,30406917
19,204,32358896
19,207,33279387
19,208,33246939
19,209,30147803
19,213,33062427
19,214,31870943
19,215,31789550
19,216,32118221
19,217,32267735
19,219,30102854
19,221,31589219
19,222,33256161
19,223,31788451
19,226,30909439
19,227,32730395
19,229,33409192
19,230,32616130
19,231,30866556
19,234,31941583
19,237,30663186
19,240,32556897
19,241,31587932
19,243,31250053
19,244,32255622
19,246,31799163
19,248,31923750
19,249,31321962
19,252,32052677
19,255,31616453
19,256,31506746
19,257,32235347
19,258,32444215
19,259,33150189
19,263,32598609
19,264,31249695
19,265,31237714
19,270,31277157
19,272,32032190
19,274,32444302
19,277,30585269
19,278,32032713
19,279,32002481
19,280,31526077
19,283,33172325
19,284,32089092
19,285,3

39,71,33636745
39,72,32197132
39,75,33192214
39,76,32347601
39,78,30557581
39,79,30776158
39,80,31794478
39,81,32358863
39,85,31525516
39,87,31984317
39,89,31797259
39,90,31897484
39,92,32427576
39,94,31009928
39,95,32285953
39,97,32067047
39,99,31943437
39,101,32710719
39,103,31586656
39,104,31378099
39,105,30828870
39,109,30990718
39,114,32697514
39,117,31194084
39,118,32592711
39,120,30678512
39,123,31671979
39,124,31151877
39,125,31833583
39,126,32698978
39,127,33749145
39,129,32185937
39,131,31277213
39,133,32274874
39,135,31754723
39,136,30086655
39,137,30399814
39,142,32078332
39,148,31411987
39,149,33442198
39,151,31237284
39,152,30531969
39,155,32113261
39,156,30468802
39,159,32379247
39,165,32317421
39,166,31890515
39,168,29887217
39,169,32683857
39,170,31527302
39,171,32872544
39,172,31486798
39,176,31556967
39,177,30225046
39,178,31852319
39,181,30629071
39,182,30882086
39,183,30137915
39,186,32808841
39,187,31664289
39,191,31543598
39,193,31560556
39,194,30968749
39,195,29

58,201,30052551
58,203,29005190
58,205,28791104
58,206,30595841
58,210,30305396
58,211,30405149
58,212,30896201
58,218,29278441
58,220,29570220
58,224,30132434
58,225,29557029
58,228,28420939
58,232,32498674
58,233,27724578
58,235,30633371
58,236,30033254
58,238,30004067
58,239,31276429
58,242,31026271
58,245,30593368
58,247,29597556
58,250,30028667
58,251,29914550
58,253,31524075
58,254,28813489
58,260,31172087
58,261,28874408
58,262,29494874
58,266,29411117
58,267,29420243
58,268,29850809
58,269,31845742
58,271,28204064
58,273,29359314
58,275,29489901
58,276,28095779
58,281,29442483
58,282,29259485
58,287,29887068
58,288,30671575
58,289,29237289
58,291,32091158
58,292,29563761
58,293,30211042
58,294,29743051
58,295,30161999
58,297,29156165
58,298,29950762
58,300,31233276
58,302,29472895
58,306,31556977
58,308,31693354
58,309,31693638
58,310,29937030
58,311,29869868
58,312,30292838
58,313,30429280
58,314,30592631
58,318,29498829
58,320,29651974
58,321,31496176
58,322,29477262
58,323,3

78,129,30829412
78,131,30060472
78,133,31406956
78,135,30570165
78,136,29280173
78,137,29602441
78,142,30949646
78,148,30796244
78,149,32094150
78,151,30926041
78,152,30240250
78,155,30681359
78,156,30728684
78,159,31205171
78,165,31654825
78,166,31088865
78,168,28441518
78,169,29787497
78,170,30908021
78,171,32502441
78,172,31289978
78,176,31716326
78,177,29991511
78,178,31924466
78,181,29946200
78,182,29544772
78,183,28438849
78,186,32062065
78,187,29901576
78,191,29464772
78,193,31699332
78,194,30738019
78,195,29061922
78,196,31161696
78,197,30542972
78,199,30851823
78,200,30698196
78,201,31158396
78,203,30701241
78,205,29391505
78,206,30909408
78,210,30467896
78,211,31174009
78,212,31112590
78,218,29116417
78,220,31067793
78,224,30557862
78,225,30080344
78,228,29614917
78,232,32245610
78,233,29026436
78,235,30424481
78,236,31059331
78,238,30580624
78,239,31003973
78,242,32390988
78,245,30312491
78,247,30665527
78,250,30194472
78,251,30127955
78,253,32349390
78,254,30820357
78,260,3

...

397,345,32774435
397,346,32456433
397,347,32697789
397,348,31929024
397,351,32607398
397,353,32552768
397,354,31115346
397,356,30462007
397,359,32820343
397,361,33712594
397,365,32354248
397,370,31146157
397,372,33500425
397,375,32304393
397,376,31520642
397,378,32212449
397,380,31655760
397,383,32755047
397,385,31172178
397,386,32175341
397,387,31625186
397,389,33402970
397,390,32702386
397,408,30973762
397,410,32562434
397,411,31355541
397,412,31736185
397,413,29867879
397,414,32520446
397,417,32944000
397,419,31306368
397,422,31449076
397,426,31171654
397,429,31071867
397,433,32246705
397,435,33169722
397,440,30170106
397,441,32021626
397,442,30616166
397,445,31758442
397,446,31519325
397,447,31686236
397,449,32182707
397,451,32794275
397,452,29746382
397,453,32739744
397,456,32652005
397,457,30993643
397,458,32161439
397,461,32333547
397,464,31092553
397,465,31758460
397,467,30586041
397,468,31554468
397,469,32628920
397,470,31693361
397,473,31622076
397,474,32179649
397,477,324091

421,192,30584405
421,198,32857090
421,202,31035456
421,204,31042524
421,207,32471139
421,208,31642955
421,209,30815851
421,213,31951377
421,214,30354029
421,215,31745136
421,216,30718921
421,217,31258910
421,219,29933078
421,221,31382883
421,222,32120007
421,223,31605321
421,226,30428875
421,227,32566197
421,229,32762183
421,230,31452920
421,231,31429965
421,234,31115349
421,237,29849323
421,240,31042862
421,241,31223761
421,243,30492324
421,244,31452556
421,246,29781990
421,248,31611190
421,249,31023037
421,252,32550241
421,255,30752172
421,256,30800463
421,257,32224657
421,258,31924863
421,259,31666357
421,263,31565034
421,264,30805444
421,265,30892940
421,270,31014606
421,272,31651452
421,274,32533386
421,277,29009467
421,278,31669421
421,279,31714459
421,280,30811271
421,283,32437553
421,284,30929333
421,285,31632080
421,286,32607149
421,290,31314717
421,296,30846343
421,299,32300849
421,301,29669660
421,303,31234994
421,304,31326476
421,305,31865351
421,307,29859488
421,315,306304

440,103,32105820
440,104,30562571
440,105,31079279
440,109,29944865
440,114,32637525
440,117,29766228
440,118,31663071
440,120,30131861
440,123,30379919
440,124,30713750
440,125,30220120
440,126,31826602
440,127,33251569
440,129,30979345
440,131,30355453
440,133,30960038
440,135,30526299
440,136,29345205
440,137,30330335
440,142,30966691
440,148,30084426
440,149,32067557
440,151,31196871
440,152,30935862
440,155,31664099
440,156,30579278
440,159,31202324
440,165,30926274
440,166,31360558
440,168,29075138
440,169,31022008
440,170,30761485
440,171,34341335
440,172,32046803
440,176,31462036
440,177,29300634
440,178,32096869
440,181,28815870
440,182,29712647
440,183,29615860
440,186,32297199
440,187,31066837
440,191,30561721
440,193,31658485
440,194,31168188
440,195,29753904
440,196,31775769
440,197,30727166
440,199,30190503
440,200,31492931
440,201,30609953
440,203,30240294
440,205,29350653
440,206,30790713
440,210,31387131
440,211,31896382
440,212,31909355
440,218,29476500
440,220,303805

460,66,30545864
460,68,30327853
460,69,32055559
460,70,30203688
460,73,32234448
460,74,31505790
460,77,32007282
460,82,30181648
460,83,31397401
460,84,30661497
460,86,31009228
460,88,31292358
460,91,32915804
460,93,31760860
460,96,30879370
460,98,31087105
460,100,31163130
460,102,31922635
460,106,31467863
460,107,32106672
460,108,31952447
460,110,32956100
460,111,30861570
460,112,31516368
460,113,30099842
460,115,31286107
460,116,31041665
460,119,29284341
460,121,32082152
460,122,31895770
460,128,30586399
460,130,31004590
460,132,31042575
460,134,31782013
460,138,30663695
460,139,31059427
460,140,30907562
460,141,30537308
460,143,31251548
460,144,31141808
460,145,31056191
460,146,32964466
460,147,30461559
460,150,30900356
460,153,28942500
460,154,31651734
460,157,33099035
460,158,31440727
460,160,31023405
460,161,32886927
460,162,31632572
460,163,30730121
460,164,30878630
460,167,29899666
460,173,32344867
460,174,30179335
460,175,30347039
460,179,31211671
460,180,30814910
460,184,31313

481,225,30644178
481,228,30332680
481,232,32263363
481,233,28222655
481,235,30946313
481,236,31176963
481,238,30759350
481,239,31736284
481,242,31773107
481,245,31000587
481,247,31877443
481,250,30630921
481,251,30546036
481,253,31881904
481,254,29694840
481,260,31936804
481,261,30125452
481,262,29350947
481,266,30584278
481,267,29990318
481,268,32104643
481,269,32449486
481,271,29483140
481,273,29840752
481,275,29110766
481,276,28789482
481,281,30228281
481,282,29621719
481,287,30383326
481,288,31120345
481,289,30052326
481,291,32855076
481,292,30948809
481,293,30583078
481,294,29833054
481,295,30547839
481,297,30245664
481,298,31897416
481,300,30856800
481,302,31138281
481,306,31230329
481,308,32114947
481,309,32442688
481,310,31174931
481,311,30320934
481,312,30534169
481,313,31076491
481,314,31560178
481,318,30203830
481,320,29225898
481,321,32616706
481,322,30048995
481,323,32507127
481,324,30305953
481,327,29952686
481,329,29032898
481,332,30164805
481,337,28063133
481,339,302726

In [17]:
#get the unique value in the row
# def get_unique_numbers(numbers):

#     list_of_unique_numbers = []

#     unique_numbers = set(numbers)

#     for number in unique_numbers:
#         list_of_unique_numbers.append(number)

#     return list_of_unique_numbers

#b 的row數 

# def getrow(list_ab):
#     a_list = entrance_a.collect()
#     b_list = entrance_b.collect()
#     rowcount = []
#     for element in range(len(list_ab)):
#         rowcount.append(list_ab[element][0])
#     return get_unique_numbers(rowcount)    
        
# row_count = len(getrow(b_list))
# print(f' #matrix-b: row數量:{row_count}') 

# # b的總長
# entrance_b.count()

# ## b rdd的shape
# b_shape = (len(getrow(b_list)),int(entrance_b.count()/len(getrow(b_list))))
# b_shape

In [18]:
# #求取a rdd shape
# entrance_a.count()

# a_shape =  (int(entrance_a.count()/len(getrow(a_list))),len(getrow(a_list)))
# a_shape